In [1]:
# Mount google drive in colab
from google.colab import drive
drive.mount('/content/drive')

# Connect kaggle in colab
!pip install -q kaggle
!mkdir -p ~/.kaggle
!cp /content/drive/MyDrive/kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

# Set the environment variable for Kaggle API key
import os
os.environ['KAGGLE_CONFIG_DIR'] = '/root/.kaggle/'

# Now you can use Kaggle API to download datasets
import kaggle
kaggle.api.authenticate()

# Replace 'username/dataset-name' with the actual dataset you want to download
kaggle.api.dataset_download_files('imperialwarrior/singapore-crypto', unzip=True)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Singaporean Cryptocurrency Analysis using DL

- Dataset from Kaggle [Link](https://www.kaggle.com/datasets/imperialwarrior/singapore-crypto?rvi=1)

### Importing necessary Modules and Libraries

In [2]:
import pandas as pd
import numpy as np
import os

import plotly.graph_objects as go

from sklearn import preprocessing
from sklearn.model_selection import train_test_split

# Different models
from sklearn.linear_model import LinearRegression, Ridge
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.tree import DecisionTreeRegressor
from xgboost import XGBRegressor


## Reading `metadata.csv` file
- It contains information about the Bit coin Pair Name and Bit Coin Pair Symbol.
- Along with that it also contains the `Filename` of that bitcoin dataset.

In [3]:
df = pd.read_csv('/content/metadata.csv')
print(df.shape)
df.head()

(7537, 3)


Coin Pair Name Coin Pair Symbol      Filename
0      Bitcoin SGD          BTC-SGD   BTC-SGD.csv
1     Ethereum SGD          ETH-SGD   ETH-SGD.csv
2  Tether USDt SGD         USDT-SGD  USDT-SGD.csv
3          BNB SGD          BNB-SGD   BNB-SGD.csv
4     USD Coin SGD         USDC-SGD  USDC-SGD.csv

### Reading about basic information of file `metadata.csv` like, unique values corresponding to the different columns.

In [4]:
print(len(df['Coin Pair Name'].unique()))
print(len(df['Coin Pair Symbol'].unique()))
print(len(df['Filename'].unique()))

7474
7537
7537


### Let's see the dataset of index 0 i.e., First dataset

In [5]:
data = pd.read_csv(os.path.join('/content/data/', df['Filename'][0]))
print(f'Unique elements correspond to Name = {len(data["Name"].unique())}')
print(f'Unique elements correspond to Symbol = {len(data["Symbol"].unique())}')
print(f'Shape: ', data.shape)
data.head()

Unique elements correspond to Name = 1
Unique elements correspond to Symbol = 1
Shape:  (3383, 9)


Name   Symbol        Date        Open        High         Low  \
0  Bitcoin SGD  BTC-SGD  2014-09-17  588.148647  591.064995  571.178236   
1  Bitcoin SGD  BTC-SGD  2014-09-18  579.204817  579.204817  523.731201   
2  Bitcoin SGD  BTC-SGD  2014-09-19  537.202785  541.930028  487.079011   
3  Bitcoin SGD  BTC-SGD  2014-09-20  499.924402  536.180566  493.856994   
4  Bitcoin SGD  BTC-SGD  2014-09-21  516.913098  522.411760  498.034510   

        Close   Adj Close    Volume  
0  577.379609  577.379609  21056800  
1  538.102924  538.102924  34483200  
2  500.080185  500.080185  37919700  
3  517.950509  517.950509  36863600  
4  505.178603  505.178603  26580100

In [6]:
data.drop(columns=['Name', 'Symbol'], inplace=True)
data.Date = pd.to_datetime(data.Date)
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3383 entries, 0 to 3382
Data columns (total 7 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   Date       3383 non-null   datetime64[ns]
 1   Open       3383 non-null   float64       
 2   High       3383 non-null   float64       
 3   Low        3383 non-null   float64       
 4   Close      3383 non-null   float64       
 5   Adj Close  3383 non-null   float64       
 6   Volume     3383 non-null   int64         
dtypes: datetime64[ns](1), float64(5), int64(1)
memory usage: 185.1 KB


### Declaring some global variables after watching the datasets.

In [7]:
filePath = '/content/data/'
target = 'Close'
check = 5
testSize = 0.2

# Training only first 25 Datasets out of 7537 datasets.
limit = 25
models = {
  'Linear Regression': LinearRegression(),
  'Ridge Regression': Ridge(),
  'Random Forest Regressor': RandomForestRegressor(),
  'Decision Tree Regressor': DecisionTreeRegressor(),
  'Gradient Boosting Regressor': GradientBoostingRegressor(),
  'XGBoost Regressor': XGBRegressor(objective ='reg:squarederror')
}

### Function which can plot the graph of the dataset

In [8]:
def plotGraph(data, name):
  figure = go.Figure(data=[go.Candlestick(x=data['Date'],
                                          open=data['Open'],
                                          high=data['High'],
                                          low=data['Low'],
                                          close=data['Close'])])

  figure.update_layout(title=name, xaxis_rangeslider_visible=False)
  figure.show()

### Splitting the dataset into training, testing, and validation dataset.

In [9]:
def splitData(dataFrame, testSize=0.2):
  # Preprocessing the datasets
  x = dataFrame[["Open", "High", "Low", "Volume"]]
  y = dataFrame[target]
  x = x.to_numpy()
  y = y.to_numpy()
  y = y.reshape(-1, 1)

  # Split the dataset into training and testing sets using train_test_split
  xtrain, xtest, ytrain, ytest = train_test_split(x, y, test_size=testSize, random_state=42)

  response = [xtrain, xtest, ytrain, ytest]
  return response


### Function to train the model and return the accuracy to that corresponding dataset.

In [10]:
def trainModel(xtrain, xtest, ytrain, ytest, fileName):
  # Create an empty DataFrame to store accuracy for the current dataset
  datasetAccuracy = pd.DataFrame(columns=['Dataset'] + list(models.keys()))

  # Store the dataset name
  datasetAccuracy['Dataset'] = [fileName]

  for modelName, model in models.items():
    # Fit the model
    model.fit(xtrain, ytrain)

    # Check the accuracy of the model and its forecasting
    score = model.score(xtest, ytest)

    # Store the accuracy in the DataFrame
    datasetAccuracy[modelName] = [score]

  return datasetAccuracy


### Function to train the dataset on all the models and get the accuracies on different models.

In [11]:
def trainModels(dataFrame):
  # Initialize an empty DataFrame to store accuracy results
  accuracyDF = pd.DataFrame(columns=['Dataset'] + list(models.keys()))

  # Iterate over only limited datasets
  for i in dataFrame.index:
    if i >= limit:
      break

    # For a single dataset
    fileName = dataFrame['Filename'][i]
    data = pd.read_csv(os.path.join(filePath, fileName))

    # Let's plot the graph of the ith dataset
    plotGraph(data, fileName)

    # Split dataset for training and testing purpose
    xtrain, xtest, ytrain, ytest = splitData(data)

    # Now, train the model and get the accuracy of all the models
    datasetAccuracy = trainModel(xtrain, xtest, ytrain, ytest, fileName[slice(-4)])

    # Append the accuracy for the current dataset to the overall DataFrame
    accuracyDF = accuracyDF.append(datasetAccuracy, ignore_index=True)

  return accuracyDF

### Calling the function to train the models on the limited dataset

(because lack of resouces like GPU, RAM, etc.)

In [12]:
# Call the trainModels function
accuracies = trainModels(df)

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=1.46304e-17): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=4.02119e-25): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=1.3842e-17): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=1.60799e-28): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



...

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=1.29537e-21): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=9.59135e-18): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=1.48274e-20): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning:

Ill-conditioned matrix (rcond=2.12519e-21): result may not be accurate.

<ipython-input-10-4521ef8e7de3>:10: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().

/usr/local/lib/python3.10/dist-packages/sklearn/ensemble/_gb.py:437: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().

<ipython-input-11-3cdfc7a83544>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



### Save accuracies of the whole training results into a single csv file named `results.csv`

In [13]:
accuracies.to_csv('results.csv', index=False)

### Let us see the saved dataset `results.csv`

In [14]:
resultsData = pd.read_csv('results.csv')
print("Accuracies of Different models on different datasets!")
resultsData

Accuracies of Different models on different datasets!


Dataset  Linear Regression  Ridge Regression  \
0        BTC-SGD           0.999703          0.999703   
1        ETH-SGD           0.999311          0.999311   
2       USDT-SGD           0.973631          0.931483   
3        BNB-SGD           0.999381          0.999381   
4       USDC-SGD           0.976592          0.880117   
5        XRP-SGD           0.986789          0.990231   
6      STETH-SGD           0.997152          0.997152   
7        ADA-SGD           0.998844          0.998843   
8       DOGE-SGD           0.997532          0.996282   
9       WTRX-SGD           0.993193          0.520164   
10       SOL-SGD           0.998861          0.998861   
11       TRX-SGD           0.994416          0.970182   
12  TON11419-SGD           0.987901          0.986923   
13       DAI-SGD           0.956892          0.863366   
14       DOT-SGD           0.997157          0.997160   
15     MATIC-SGD           0.998655          0.998550   
16       LTC-SGD           0.998378          0.998378   
17      WBTC-SGD           0.998118          0.998118   
18      SHIB-SGD           0.997543          0.348902   
19       BCH-SGD           0.998268          0.998268   
20       XLM-SGD           0.996184          0.994903   
21       LEO-SGD           0.998021          0.997750   
22      AVAX-SGD           0.997976          0.997976   
23      LINK-SGD           0.998810          0.998809   
24      TUSD-SGD           0.922381          0.877465   

    Random Forest Regressor  Decision Tree Regressor  \
0                  0.999468                 0.999053   
1                  0.998623                 0.998094   
2                  0.965214                 0.950597   
3                  0.998764                 0.998167   
4                  0.980140                 0.969791   
5                  0.991697                 0.987660   
6                  0.995287                 0.993184   
7                  0.998173                 0.995809   
8                  0.996732                 0.995176   
9                  0.985621                 0.979841   
10                 0.997650                 0.997153   
11                 0.981699                 0.985031   
12                 0.980488                 0.955144   
13                 0.969210                 0.955764   
14                 0.996588                 0.993182   
15                 0.996827                 0.993972   
16                 0.997971                 0.995632   
17                 0.992431                 0.997462   
18                 0.977479                 0.956806   
19                 0.995707                 0.992923   
20                 0.995776                 0.989450   
21                 0.991283                 0.989968   
22                 0.995018                 0.990893   
23                 0.997424                 0.995608   
24                 0.976368                 0.961560   

    Gradient Boosting Regressor  XGBoost Regressor  
0                      0.999401           0.999357  
1                      0.998480           0.998446  
2                      0.963910           0.966679  
3                      0.998875           0.998626  
4                      0.977137           0.979106  
5                      0.991987           0.991860  
6                      0.995217           0.994591  
7                      0.997596           0.997686  
8                      0.996231           0.994917  
9                      0.986519           0.981738  
10                     0.997514           0.997196  
11                     0.984792           0.980132  
12                     0.981399           0.974923  
13                     0.970992           0.966129  
14                     0.996363           0.995526  
15                     0.997526           0.996792  
16                     0.997830           0.996950  
17                     0.994908           0.991558  
18                     0.983012          -0.004916  
19       

#### Hence, Model training completed, and accuracy of all models on different dataset is stored in the CSV file.

---

## Let's now train the model on LSTM model

In [15]:
from keras.models import Sequential
from keras.layers import Dense, LSTM
from sklearn.metrics import mean_squared_error, r2_score


#### Now, prepare the LSTM Neural Network

In [16]:
def lstmNeuralNetwork(shape):
  # LSTM neural network building
  model = Sequential()
  model.add(LSTM(128, return_sequences=True, input_shape=(shape, 1)))
  model.add(LSTM(64, return_sequences=False))
  model.add(Dense(25))
  model.add(Dense(1))
  model.summary()
  return model


#### Let's train the model and fit the dataset on the model

In [17]:
def lstmTrain(xtrain, ytrain, xtest, ytest, model, epochs=30, batchSize=1):
  # Compile this model and fit the dataset on the model
  model.compile(optimizer='adam', loss='mean_squared_error')
  model.fit(xtrain, ytrain, batch_size=batchSize, epochs=epochs)

  predictions = model.predict(xtest)

  # Calculate Mean Squared Error
  mse = mean_squared_error(ytest, predictions)

  # Calculate R2 Score
  r2 = r2_score(ytest, predictions)

  return {'mse': mse, 'r2': r2}


#### Iterate over all the datasets and fit the on the model and store the accuracy of the model on that corresponding dataset

In [18]:
def lstmModelTrain(dataFrame):
  # Create an empty DataFrame to store accuracy results
  accuracyDF = pd.DataFrame(columns=['Dataset', 'MSE', 'R2'])

  # LSTM model building
  model = lstmNeuralNetwork(4)

  # Iterate over only limited datasets
  for i in dataFrame.index:
    if i >= limit:
      break

    # For a single dataset
    fileName = dataFrame['Filename'][i]
    data = pd.read_csv(os.path.join(filePath, fileName))

    # Split dataset for training and testing purpose
    xtrain, xtest, ytrain, ytest = splitData(data)

    # Now, train the model and get the accuracy of all the models
    accuracy = lstmTrain(xtrain, ytrain, xtest, ytest, model, 20)

    # Append the accuracy for the current dataset to the overall DataFrame
    accuracyDF = accuracyDF.append({'Dataset': fileName[slice(-4)], 'MSE': accuracy['mse'], 'R2': accuracy['r2']}, ignore_index=True)

  return accuracyDF


### Calling the function to train the models on the limited dataset

(because lack of resouces like GPU, RAM, etc.)

In [19]:
# Call the trainModels function
accuracies = lstmModelTrain(df)

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 4, 128)            66560     
                                                                 
 lstm_1 (LSTM)               (None, 64)                49408     
                                                                 
 dense (Dense)               (None, 25)                1625      
                                                                 
 dense_1 (Dense)             (None, 1)                 26        
                                                                 
Total params: 117619 (459.45 KB)
Trainable params: 117619 (459.45 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
Epoch 1/20
2706/2706 [==============================] - 18s 5ms/step - loss: 745167104.0000
Epoch 2/20
2706/2706 [==============================] - 

<ipython-input-18-260e4fbff9f2>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



1787/1787 [==============================] - 12s 5ms/step - loss: 28121298.0000
Epoch 2/20
1787/1787 [==============================] - 8s 5ms/step - loss: 4415281.5000
Epoch 3/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3828182.0000
Epoch 4/20
1787/1787 [==============================] - 8s 4ms/step - loss: 3561334.7500
Epoch 5/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3261703.0000
Epoch 6/20
1787/1787 [==============================] - 9s 5ms/step - loss: 2911701.0000
Epoch 7/20
1787/1787 [==============================] - 9s 5ms/step - loss: 2608607.0000
Epoch 8/20
1787/1787 [==============================] - 10s 5ms/step - loss: 2425824.7500
Epoch 9/20
1787/1787 [==============================] - 8s 5ms/step - loss: 2340636.2500
Epoch 10/20
1787/1787 [==============================] - 11s 6ms/step - loss: 1795463.1250
Epoch 11/20
1787/1787 [==============================] - 9s 5ms/step - loss: 1198625.7500
Epoch 12/20
1787/1787 [===

<ipython-input-18-260e4fbff9f2>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



1787/1787 [==============================] - 12s 5ms/step - loss: 12907430.0000
Epoch 2/20
1787/1787 [==============================] - 9s 5ms/step - loss: 252.9839
Epoch 3/20
1787/1787 [==============================] - 8s 5ms/step - loss: 32.2892
Epoch 4/20
1787/1787 [==============================] - 9s 5ms/step - loss: 33.7245
Epoch 5/20
1787/1787 [==============================] - 8s 5ms/step - loss: 36.0902
Epoch 6/20
1787/1787 [==============================] - 9s 5ms/step - loss: 43.2694
Epoch 7/20
1787/1787 [==============================] - 9s 5ms/step - loss: 35.8518
Epoch 8/20
1787/1787 [==============================] - 9s 5ms/step - loss: 27.0522
Epoch 9/20
1787/1787 [==============================] - 9s 5ms/step - loss: 21.3199
Epoch 10/20
1787/1787 [==============================] - 8s 4ms/step - loss: 14.8917
Epoch 11/20
1787/1787 [==============================] - 9s 5ms/step - loss: 12.3881
Epoch 12/20
1787/1787 [==============================] - 9s 5ms/step - loss: 

...

<ipython-input-18-260e4fbff9f2>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



1787/1787 [==============================] - 12s 5ms/step - loss: 5.2036
Epoch 2/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3.2617
Epoch 3/20
1787/1787 [==============================] - 8s 5ms/step - loss: 3.7946
Epoch 4/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3.3587
Epoch 5/20
1787/1787 [==============================] - 8s 4ms/step - loss: 2.7498
Epoch 6/20
1787/1787 [==============================] - 9s 5ms/step - loss: 2.9537
Epoch 7/20
1787/1787 [==============================] - 8s 5ms/step - loss: 3.8335
Epoch 8/20
1787/1787 [==============================] - 9s 5ms/step - loss: 2.6072
Epoch 9/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3.8192
Epoch 10/20
1787/1787 [==============================] - 11s 6ms/step - loss: 3.3862
Epoch 11/20
1787/1787 [==============================] - 9s 5ms/step - loss: 3.0701
Epoch 12/20
1787/1787 [==============================] - 9s 5ms/step - loss: 6.7764
Epoch 13/2

<ipython-input-18-260e4fbff9f2>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



1693/1693 [==============================] - 12s 4ms/step - loss: 0.0056
Epoch 2/20
1693/1693 [==============================] - 9s 5ms/step - loss: 0.0025
Epoch 3/20
1693/1693 [==============================] - 8s 5ms/step - loss: 0.0027
Epoch 4/20
1693/1693 [==============================] - 9s 5ms/step - loss: 0.0031
Epoch 5/20
1693/1693 [==============================] - 8s 5ms/step - loss: 0.0026
Epoch 6/20
1693/1693 [==============================] - 8s 5ms/step - loss: 0.0027
Epoch 7/20
1693/1693 [==============================] - 9s 5ms/step - loss: 0.0027
Epoch 8/20
1693/1693 [==============================] - 8s 4ms/step - loss: 0.0021
Epoch 9/20
1693/1693 [==============================] - 9s 5ms/step - loss: 0.0022
Epoch 10/20
1693/1693 [==============================] - 8s 5ms/step - loss: 0.0027
Epoch 11/20
1693/1693 [==============================] - 9s 5ms/step - loss: 0.0019
Epoch 12/20
1693/1693 [==============================] - 8s 5ms/step - loss: 0.0027
Epoch 13/20

<ipython-input-18-260e4fbff9f2>:24: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



### Save accuracies of the whole training results into a single csv file named `LSTM_results.csv`

In [21]:
accuracies.to_csv('LSTM_results.csv', index=False)

### Let us see the saved dataset `LSTM_results.csv`

In [22]:
resultsData = pd.read_csv('LSTM_results.csv')
print("Accuracies of Different models on different datasets!")
resultsData

Accuracies of Different models on different datasets!


Dataset           MSE            R2
0        BTC-SGD  4.874616e+08 -2.967174e-03
1        ETH-SGD  4.178541e+05  8.166412e-01
2       USDT-SGD  9.260454e-03 -1.327946e+01
3        BNB-SGD  1.206636e+03  9.780038e-01
4       USDC-SGD  3.359622e-03 -3.264993e+00
5        XRP-SGD  9.766995e-03  9.486673e-01
6      STETH-SGD  1.526732e+06 -1.275546e-04
7        ADA-SGD  1.603251e-02  9.681617e-01
8       DOGE-SGD  1.651918e-04  9.867902e-01
9       WTRX-SGD  4.497436e+00 -1.339005e+04
10       SOL-SGD  3.572016e+01  9.941831e-01
11       TRX-SGD  8.185882e-05  9.484200e-01
12  TON11419-SGD  2.037028e-01  7.976267e-01
13       DAI-SGD  3.348528e-03 -2.914893e+00
14       DOT-SGD  1.914015e+00  9.930964e-01
15     MATIC-SGD  1.430557e-02  9.805211e-01
16       LTC-SGD  3.159578e+01  9.956645e-01
17      WBTC-SGD  4.120300e+08 -5.060852e-03
18      SHIB-SGD  5.596118e+01 -1.915391e+11
19       BCH-SGD  8.338073e+03  9.750366e-01
20       XLM-SGD  9.369997e-04  9.683078e-01
21       LEO-SGD  6.229320e-02  9.858775e-01
22      AVAX-SGD  8.377987e+00  9.945632e-01
23      LINK-SGD  9.121696e-01  9.942063e-01
24      TUSD-SGD  9.360150e-03 -1.270343e+01

#### Model Building and LSTM Analysis Completed!

---